In [2]:
# pip install earthengine-api
import ee
import geopandas as gpd
import json
import pandas as pd
import geemap as ui
from zipfile import ZipFile
from fiona.drvsupport import supported_drivers
import os, sys


In [3]:
service_account = 'gee-ine@ee-ricpizarrosine.iam.gserviceaccount.com'
credentials = ee.ServiceAccountCredentials(service_account, 'privatekey.json')
ee.Initialize(credentials)

In [11]:
""" import geopandas as gpd
import pandas as pd
#from samgeo import  tms_to_geotiff
from fiona.drvsupport import supported_drivers
#import leafmap
import os
import re
from zipfile import ZipFile

 

################
# CARGAR DATOS #
################
 

# Abrir archivo con polígonos de la RM
poligonos =  "KMZ_UPMs_Gran_Santiago.kmz"
#supported_drivers['KML'] = 'rw'
supported_drivers['LIBKML'] = 'rw'

kmz = ZipFile(poligonos, 'r')
kmz.extract('doc.kml', "tempDir")

poligonos = gpd.read_file(os.path.join("tempDir",'doc.kml'))
 """

In [20]:

""" poligonos =  "KMZ_UPMs_Gran_Santiago.kmz"
kmz = ZipFile(poligonos, 'r')
kml = kmz.open('doc.kml', 'r').read()

print(kml) """

""" poligonos =  "KMZ_UPMs_Gran_Santiago.kmz"
supported_drivers['LIBKML'] = 'rw'
kmz = ZipFile(poligonos, 'r')
kmz.extract('doc.kml', "tempDir")


shapefile = gpd.read_file(os.path.join("tempDir",'doc.kml'))

print(shapefile.geometry.name) """


geometry


" features = []\nfor i in range(shapefile.shape[0]):\n    geom = shapefile.iloc[i:i+1,:] \n    jsonDict = eval(geom.to_json()) \n    geojsonDict = jsonDict['features'][0] \n    features.append(ee.Feature(geojsonDict)) \n\nfc = ee.FeatureCollection(features) "

In [11]:

shapefile = gpd.read_file("Manzanas/pob_manzana_censo2017.shp")

#shapefile = gpd.read_file("gran_santiago/gran_santiago.shp")

print(len(shapefile))

#shapefile = shapefile.iloc[0:1500,]

158927


In [16]:
type(shapefile)

shapefile.attrs

import numpy as np

In [19]:
mylist = [[i+1]*400 for i in range(len(shapefile))]
mylist

[[1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,


In [20]:
shapefile['group_id'] = np.resize(mylist,len(shapefile))
shapefile["group_id"].max()

398

In [5]:

features = []
for i in range(shapefile.shape[0]):
    geom = shapefile.iloc[i:i+1,:] 
    jsonDict = eval(geom.to_json()) 
    geojsonDict = jsonDict['features'][0] 
    features.append(ee.Feature(geojsonDict)) 

fc = ee.FeatureCollection(features)


In [6]:

Map = ui.Map()
Map.addLayer (fc,{
  },
'fc')

Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

In [10]:
def add_ndvi(image):
    # Normalized difference vegetation index (NDVI)
    ndvi = image.normalizedDifference(['B8','B4']).rename("NDVI")
    image = image.addBands(ndvi)
    return(image)


def addDate(image):
    img_date = ee.Date(image.date())
    img_date = ee.Number.parse(img_date.format('YYYYMMdd'))
    return image.addBands(ee.Image(img_date).rename('date').toInt())
    
# Import the Sentinel-2 image collection
S2_SR = ee.ImageCollection('COPERNICUS/S2_SR_HARMONIZED')\
          .filterBounds(fc)\
          .filterDate('2021-01-01', '2022-01-07')\
          .map(add_ndvi).map(addDate)
#
print('Image collection:', S2_SR.first().getInfo())
 

Image collection: {'type': 'Image', 'bands': [{'id': 'B1', 'data_type': {'type': 'PixelType', 'precision': 'int', 'min': 0, 'max': 65535}, 'dimensions': [1830, 1830], 'crs': 'EPSG:32719', 'crs_transform': [60, 0, 300000, 0, -60, 7800040]}, {'id': 'B2', 'data_type': {'type': 'PixelType', 'precision': 'int', 'min': 0, 'max': 65535}, 'dimensions': [10980, 10980], 'crs': 'EPSG:32719', 'crs_transform': [10, 0, 300000, 0, -10, 7800040]}, {'id': 'B3', 'data_type': {'type': 'PixelType', 'precision': 'int', 'min': 0, 'max': 65535}, 'dimensions': [10980, 10980], 'crs': 'EPSG:32719', 'crs_transform': [10, 0, 300000, 0, -10, 7800040]}, {'id': 'B4', 'data_type': {'type': 'PixelType', 'precision': 'int', 'min': 0, 'max': 65535}, 'dimensions': [10980, 10980], 'crs': 'EPSG:32719', 'crs_transform': [10, 0, 300000, 0, -10, 7800040]}, {'id': 'B5', 'data_type': {'type': 'PixelType', 'precision': 'int', 'min': 0, 'max': 65535}, 'dimensions': [5490, 5490], 'crs': 'EPSG:32719', 'crs_transform': [20, 0, 30000

In [9]:
# # Select the NDVI band

veget = S2_SR.select('NDVI')

veget_red = veget.reduce(ee.Reducer.mean())

veget_red


NameError: name 'S2_SR' is not defined

In [8]:

Map = ui.Map()

paletaPL=['red','white','green']

Map.addLayer (veget_red,{
  'min': -0.5,
  'max': 0.5,
  'palette':paletaPL
  },
'NDVI')

Map

NameError: name 'veget_red' is not defined

In [16]:
### Calculate the mean NDVI inside each polygon(buffer)
import geemap

def calcmean(feature):
      reduced = veget_red.reduceRegions(
                collection = feature,
                reducer = ee.Reducer.mean(),
                scale = 10)
      return reduced

final = fc.map(calcmean).flatten()

print(final.getInfo())

df = geemap.ee_to_pandas(final)


df.to_csv('fe_2023.csv')

{'type': 'FeatureCollection', 'columns': {}, 'features': [{'type': 'Feature', 'geometry': {'type': 'Polygon', 'coordinates': [[[-70.6768337349999, -33.42769344], [-70.676833985, -33.4276903529999], [-70.676903381, -33.426832878], [-70.676904119, -33.426823762], [-70.67690534, -33.426808679], [-70.6769224239999, -33.426785003], [-70.676931849, -33.426771942], [-70.676940341, -33.4267601729999], [-70.676951887, -33.4267441719999], [-70.6769675159999, -33.426722513], [-70.676987002, -33.4266955099999], [-70.677022299, -33.4266465929999], [-70.6770617619999, -33.426591905], [-70.677165099, -33.426594087], [-70.6772702819999, -33.426603401], [-70.677382306, -33.426613339], [-70.677510105, -33.4266445379999], [-70.677659572, -33.4266926239999], [-70.677909114, -33.42679519], [-70.677984151, -33.426834976], [-70.678060085, -33.426868053], [-70.6780601629999, -33.4268680869999], [-70.678060242, -33.426868121], [-70.678101028, -33.426885888], [-70.678154207, -33.426909053], [-70.6781756399999, 